## Import / Config

In [ ]:
import pandas as pd
from sqlalchemy import create_engine

# In die Datei const.py müssen die Zugangsdaten eingetragen werden
import const as c
import folium

In [ ]:
def lat_lng_from_sql(sql, engine):
    with engine.connect() as con:
        lat_lng_df = pd.read_sql_query(sql, con)
    return lat_lng_df.iat[0,0], lat_lng_df.iat[0,1]

def geojson_from_sql(sql, engine):
    with engine.connect() as con:
        lat_lng_df = pd.read_sql_query(sql, con)
    return lat_lng_df.iat[0,0]
 

## Engine

In [ ]:
engine = create_engine(
    f'postgresql://{c.pg_userid}:{c.pg_password}@{c.pg_host}/{c.pg_db}', 
    connect_args = {'options': '-c search_path=uadbkt,umobility,public', 'keepalives_idle': 120},
    pool_size=1, 
    max_overflow=0,
    execution_options={ 'isolation_level': 'AUTOCOMMIT' }
)

In [ ]:
# engine.dispose()

## HTW

In [ ]:
sql_htw_lat_lng = """
select ST_Y(ST_Centroid(geometry)) as lat, ST_X(ST_Centroid(geometry)) as lng
from gis_osm_pois_a_free_1 
where osm_id ='41361350'
order by fclass, name; 
"""

htw_lat, htw_lng = lat_lng_from_sql(sql_htw_lat_lng, engine)
htw_lat, htw_lng
map_htw = folium.Map(location=[htw_lat, htw_lng], zoom_start=17)
folium.Marker(
    location=[htw_lat, htw_lng],
    tooltip="HTW"
).add_to(map_htw)

sql_htw_geojson = """
select ST_AsGeoJSON(geometry)
from gis_osm_pois_a_free_1 
where osm_id ='41361350'
order by fclass, name; 
"""
htw_geojson = geojson_from_sql(sql_htw_geojson, engine)
folium.GeoJson(htw_geojson).add_to(map_htw)
map_htw

## Bezirke

In [ ]:
latlng_berlin = [52.5170365, 13.3888599]
map_berlin = folium.Map(location=latlng_berlin, zoom_start=10)
sql_bezirke_geojson = """
select name as bname, ST_AsGeoJSON(shape) as geojson
from bezirk; 
"""
with engine.connect() as con:
    bezirke_geojson_df = pd.read_sql_query(
        sql_bezirke_geojson, con)

for b in bezirke_geojson_df.apply(
        lambda r: folium.GeoJson(r.geojson), axis=1):
    b.add_to(map_berlin)
sql_bezirke_centroid_geojson = """
select 
  name as bname, 
  ST_Y(ST_Centroid(shape)) as clat, 
  ST_X(ST_Centroid(shape)) as clng
from bezirk;
"""
with engine.connect() as con:
    bezirke_centroid_geojson_df = pd.read_sql_query(
        sql_bezirke_centroid_geojson, con
    )

def cmarker(r):
    loc = [r.clat, r.clng]
    html = f'<font color="green">{r.bname}</font>'
    divicon = folium.DivIcon(html=html)
    return folium.Marker(location=loc, icon=divicon)

for bc in bezirke_centroid_geojson_df.apply(
        lambda r: cmarker(r), axis=1):
    bc.add_to(map_berlin)
sql_bb_berlin = """
select ST_AsGeoJSON(ST_Extent(shape)) as bbox
from bezirk; 
"""
bb_berlin = geojson_from_sql(sql_bb_berlin, engine)
folium.GeoJson(bb_berlin).add_to(map_berlin)
map_berlin

## Haltestellen

In [ ]:
latlng_haltestellen = [52.5170365, 13.3888599]
map_haltestellen = folium.Map(location=latlng_haltestellen, zoom_start=13)
sql_voronoi = """
select ST_AsGeoJSON(
    ST_Transform((st_dump(ST_VoronoiPolygons(
        st_collect(h.posp)))).geom, 4326)
    ) as geojson
from haltestelle h
"""
with engine.connect() as con:
    voronoi_df = pd.read_sql_query(sql_voronoi, con)

for v in voronoi_df.apply(
        lambda r: folium.GeoJson(r.geojson), axis=1):
    v.add_to(map_haltestellen)
sql_haltestellen = """
select bez, lat, lng
from haltestelle;
"""
with engine.connect() as con:
    haltestellen_df = pd.read_sql_query(sql_haltestellen, con)

def hcircle(r):
    loc = [r.lat, r.lng]
    return folium.Circle(
        location=loc, radius=20, 
        fill=True, fill_color="blue", 
        tooltip=r.bez
    )

for h in haltestellen_df.apply(
        lambda r: hcircle(r), axis=1):
    h.add_to(map_haltestellen)
map_haltestellen

## Straßenpunkte

In [ ]:
sql_htw_lat_lng = """
select ST_Y(ST_Centroid(geometry)) as lat, ST_X(ST_Centroid(geometry)) as lng
from gis_osm_pois_a_free_1 
where osm_id ='41361350'; 
"""

htw_lat, htw_lng = lat_lng_from_sql(sql_htw_lat_lng, engine)
htw_lat, htw_lng
map_htw_stadtteil = folium.Map(location=[htw_lat, htw_lng], zoom_start=14)
folium.Marker(
    location=[htw_lat, htw_lng],
    tooltip="HTW"
).add_to(map_htw_stadtteil)

sql_htw_stadtteil = """
with 
  htw_c as (
    select ST_Centroid(geometry) as c
    from gis_osm_pois_a_free_1 
    where osm_id ='41361350'
  )
select ST_AsGeoJSON(geometry)
from gis_osm_places_a_free_1 p, htw_c 
where ST_Covers(p.geometry, htw_c.c);
"""

htw_stadtteil = geojson_from_sql(sql_htw_stadtteil, engine)
folium.GeoJson(htw_stadtteil).add_to(map_htw_stadtteil)

sql_nodes = """
with 
  htw_c as (
    select ST_Centroid(geometry) as c
    from gis_osm_pois_a_free_1 
    where osm_id ='41361350'
  ),
  htw_s as (
    select geometry
      from gis_osm_places_a_free_1 p, htw_c 
      where ST_Covers(p.geometry, htw_c.c)
  )
select y as lat, x as lng, street_count, highway
from bln_nodes bn, htw_s
where ST_Covers(htw_s.geometry, bn.geometry);
 
"""
with engine.connect() as con:
    nodes_df = pd.read_sql_query(sql_nodes, con)

def scircle(r):
    loc = [r.lat, r.lng]
    return folium.Circle(
        location=loc, radius=3, 
        fill=True, fill_color="blue"
    )

for h in nodes_df.apply(
        lambda r: scircle(r), axis=1):
    h.add_to(map_htw_stadtteil)



map_htw_stadtteil

## Straßen

In [ ]:
sql_htw_lat_lng = """
select ST_Y(ST_Centroid(geometry)) as lat, ST_X(ST_Centroid(geometry)) as lng
from gis_osm_pois_a_free_1 
where osm_id ='41361350'; 
"""

htw_lat, htw_lng = lat_lng_from_sql(sql_htw_lat_lng, engine)
htw_lat, htw_lng
map_htw_stadtteil = folium.Map(location=[htw_lat, htw_lng], zoom_start=14)
folium.Marker(
    location=[htw_lat, htw_lng],
    tooltip="HTW"
).add_to(map_htw_stadtteil)

sql_htw_stadtteil = """
with 
  htw_c as (
    select ST_Centroid(geometry) as c
    from gis_osm_pois_a_free_1 
    where osm_id ='41361350'
  )
select ST_AsGeoJSON(geometry)
from gis_osm_places_a_free_1 p, htw_c 
where ST_Covers(p.geometry, htw_c.c);
"""

htw_stadtteil = geojson_from_sql(sql_htw_stadtteil, engine)
folium.GeoJson(htw_stadtteil).add_to(map_htw_stadtteil)

sql_edges = """
with 
  htw_c as (
    select ST_Centroid(geometry) as c
    from gis_osm_pois_a_free_1 
    where osm_id ='41361350'
  ),
  htw_s as (
    select geometry
      from gis_osm_places_a_free_1 p, htw_c 
      where ST_Covers(p.geometry, htw_c.c)
  )
select ST_AsGeoJSON(be.geometry) as geojson
from bln_edges be, htw_s
where ST_Covers(htw_s.geometry, be.geometry);
"""
with engine.connect() as con:
    edges_geojson_df = pd.read_sql_query(sql_edges, con)

for b in edges_geojson_df.apply(
        lambda r: folium.GeoJson(r.geojson), axis=1):
    b.add_to(map_htw_stadtteil)

map_htw_stadtteil